In [1]:
import sys
import os
import pandas as pd
import numpy as np

PROJECT_ROOT = os.path.abspath(os.path.join(os.getcwd(), "..", ".."))
if PROJECT_ROOT not in sys.path:
    sys.path.insert(0, PROJECT_ROOT)

In [2]:
DATA_PATH = os.path.join(PROJECT_ROOT, "data")
PATH_RATINGS = os.path.join(DATA_PATH, "raw_data", "kaggle_second_sem", "books_rating.csv")
PATH_BOOKS = os.path.join(DATA_PATH, "raw_data", "kaggle_second_sem", "books_data.csv")
PATH_EMBDS = os.path.join(DATA_PATH, "embeddings", "expanded_embds_ss.npy")

df_books = pd.read_csv(PATH_BOOKS)
df_ratings = pd.read_csv(PATH_RATINGS)
book_embds = np.load(PATH_EMBDS, allow_pickle=True)

In [3]:
df_ratings.head()

Id                           Title  Price         User_id  \
0  1882931173  Its Only Art If Its Well Hung!    NaN   AVCGYZL8FQQTD   
1  0826414346        Dr. Seuss: American Icon    NaN  A30TK6U7DNS82R   
2  0826414346        Dr. Seuss: American Icon    NaN  A3UH4UZ4RSVO82   
3  0826414346        Dr. Seuss: American Icon    NaN  A2MVUWT453QH61   
4  0826414346        Dr. Seuss: American Icon    NaN  A22X4XUPKF66MR   

                          profileName review/helpfulness  review/score  \
0               Jim of Oz "jim-of-oz"                7/7           4.0   
1                       Kevin Killian              10/10           5.0   
2                        John Granger              10/11           5.0   
3  Roy E. Perry "amateur philosopher"                7/7           4.0   
4     D. H. Richards "ninthwavestore"                3/3           4.0   

   review/time                                   review/summary  \
0    940636800           Nice collection of Julie Strain images   
1   1095724800                                Really Enjoyed It   
2   1078790400  Essential for every personal and Public Library   
3   1090713600  Phlip Nel gives silly Seuss a serious treatment   
4   1107993600                           Good academic overview   

                                         review/text  
0  This is only for Julie Strain fans. It's a col...  
1  I don't care much for Dr. Seuss but after read...  
2  If people become the books they read and if "t...  
3  Theodore Seuss Geisel (1904-1991), aka &quot;D...  
4  Philip Nel - Dr. Seuss: American IconThis is b...

Try to see if users even have more than one review.

In [ ]:
def print_reviews_by_user(user_id):
    user_reviews = df_ratings[df_ratings["User_id"] == user_id]

    if user_reviews.empty:
        print(f"No reviews found for user {user_id}")
    else:
        print(f"Reviews by user {user_id}:")
        for _, row in user_reviews.iterrows():
            title = row.get("Title", "Unknown Title")
            rating = row.get("review/score", "No Rating")
            print(f" - {title} | Rating: {rating}")

print_reviews_by_user("AVCGYZL8FQQTD")


Reviews by user AVCGYZL8FQQTD:
 - Its Only Art If Its Well Hung! | Rating: 4.0
 - Six Foot One and Worth the Climb | Rating: 4.0
 - Under Fire - A Corps Novel | Rating: 4.0


Remove nans

In [ ]:
df_ratings['Title'] = df_ratings['Title'].astype(str)  
df_ratings['Title'] = df_ratings['Title'].replace('nan', '')  
df_ratings = df_ratings.dropna(subset=['Title'])  

Find sequences of books that are present in multiple user's ratings. Worked on samples of datasets but entire dataset is too big and i dont have time.
Also try to remove duplicates and keep only unique sequences.

In [ ]:
import re
from pymining import seqmining
from collections import Counter

df_ratings['Title'] = df_ratings['Title'].astype(str).str.strip()
df_ratings = df_ratings[df_ratings['Title'].astype(bool)]

def normalize_title(title):
    return re.split(r'[\(\[\{;:]', title)[0].strip().lower()

df_ratings['Normalized'] = df_ratings['Title'].apply(normalize_title)

def get_unique_title_sequence(group):
    seen = set()
    sequence = []
    for title, norm in zip(group['Title'], group['Normalized']):
        if norm not in seen:
            seen.add(norm)
            sequence.append(title)
    return sequence

ratings_seqs = df_ratings.groupby("User_id").apply(get_unique_title_sequence)

ratings_seqs = ratings_seqs[ratings_seqs.apply(lambda x: len(x) > 3)]

total_seqs = len(ratings_seqs)
book_counts = Counter(
    normalize_title(book) for seq in ratings_seqs for book in set(seq)
)
too_common_books = {book for book, count in book_counts.items() if count / total_seqs > 0.95}

filtered_seqs = [
    [book for book in seq if normalize_title(book) not in too_common_books]
    for seq in ratings_seqs
]

filtered_seqs = [seq for seq in filtered_seqs if len(seq) > 1]

unique_seqs = list(set(tuple(seq) for seq in filtered_seqs))

result = seqmining.freq_seq_enum(unique_seqs, min_support=2)
result = sorted(result, key=lambda x: x[1], reverse=True)

C:\Users\пк\AppData\Local\Temp\ipykernel_29708\2387120705.py:31: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  ratings_seqs = df_ratings.groupby("User_id").apply(get_unique_title_sequence)


KeyboardInterrupt: 

In [ ]:
for pattern, count in result:
    if len(pattern) > 3:
        print(f"{pattern} — {count}")


('The Lord of the Rings Box Set', 'The Lord of the Rings Trilogy: Three Volumes in Slipcase', 'The Lord Of The Rings THREE VOLUME BOXED SET (The Fellowship Of The Ring, The Return of The King, The Two towers)', 'The Lord of the Rings (3 Volume Set)') — 6
("Alice's Adventures in Wonderland and Through the Looking Glass", "Alice's Adventures in Wonderland & Through the Looking-Glass", 'Alice in Wonderland and Through the Looking Glass', "Alice's adventures in wonderland: And Through the looking-glass, and what Alice found there,") — 6
('The Hobbit', 'The Hobbit or There and Back Again', 'The Hobbit There and Back Again', 'The Hobbitt, or there and back again; illustrated by the author.') — 5
('The Lord of the Rings Trilogy: Three Volumes in Slipcase', 'The Lord Of The Rings THREE VOLUME BOXED SET (The Fellowship Of The Ring, The Return of The King, The Two towers)', 'The Lord of the Rings Trilogy 3 Volumes', 'The Lord of the Rings (3 Volume Set)') — 5
('The Lord of the Rings (3 Volume Se